# This notebook shows Poisson-Disc sampling on a single face and compares it with random sampling

In [1]:
from pyntcloud import PyntCloud
from pyntcloud.geometry.areas import *
import math
import pandas as pd

from rotations import *
from sklearn import preprocessing
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

%matplotlib notebook

In [2]:
def is_on_face(s,a,b,c, debug=True):
    # s is the new point
    # function assumes the face has been transformed to the xy-plane
    if len(s) == 2:
        s = (s[0],s[1],0)
    
    
    # Calculate area of triangle ABC 
    A = triangle_area((a,b,c)) #(a[0], a[1], b[0], b[1], c[0], c[1]) 
  
    # Calculate area of triangle PBC  
    A1 = triangle_area((s,b,c))#area (s[0], s[1], b[0], b[1], c[0], c[1]) 
      
    # Calculate area of triangle PAC  
    A2 = triangle_area((a,s,c))#area (a[0], a[1], s[0], s[1], c[0], c[1]) 
      
    # Calculate area of triangle PAB  
    A3 = triangle_area((a,b,s)) #area (a[0], a[1], b[0], b[1], s[0], s[1]) 
      
    # Check if sum of A1, A2 and A3  
    # is same as A 
    if (debug == True):
        print(">>",A,(A1 + A2 + A3))
        
    return math.isclose(A, (A1 + A2 + A3), abs_tol=10**-1)
#     if(A == A1 + A2 + A3): 
#         return True
#     else: 
#         return False


def find_width_height(v1,v2,v3):
    
    x_min, y_min, z_min, x_max, y_max, z_max = find_minmax(v1,v2,v3)
                
    width = (x_max-x_min)
    height = (y_max-y_min)
    return width, height

def find_minmax(v1,v2,v3):
    x_min = v1[0]
    x_max = v1[0]
    y_min = v1[1]
    y_max = v1[1]
    z_min = v1[2]
    z_max = v1[2]
    left_most = v1          
    # find x_min/max and y_min/max  
    for x,y,z in (v1, v2, v3):
        if x > x_max:
            x_max = x
        if x < x_min:
            x_min = x
        if y > y_max:
            y_max = y
        if y < y_min:
            y_min = y
        if z > z_max:
            z_max = z
        if z < z_min:
            z_min = z
    return x_min, y_min, z_min, x_max, y_max, z_max

In [3]:
diamond = PyntCloud.from_file('bed_0001.off')

v1, v2, v3 = diamond.get_mesh_vertices(False, False)

v1_xyz = v1[:, :3]
v2_xyz = v2[:, :3]
v3_xyz = v3[:, :3]

areas = triangle_area_multi(v1_xyz, v2_xyz, v3_xyz)
probabilities = areas / np.sum(areas)

v1 = v1_xyz[70] #Choosing an arbitrary face to test on
v2 = v2_xyz[70]
v3 = v3_xyz[70]

originals = (v1,v2,v3)

origin_point = find_minmax(v1,v2,v3)[0:3]

# Translate face such that origin_point is the origin
translation = origin_point
v1,v2,v3,origin_point = [np.subtract(p, translation) for p in (v1,v2,v3,origin_point)] # make list or dict eventually


# rotate the face to become the xy-plane
angle = None
z_axis = (0.,0.,1.)
AB = np.subtract(v2,v1)
AC = np.subtract(v3,v1)

normal = np.cross(AB, AC)



rot_axis = np.cross(normal, z_axis)
if (np.linalg.norm(rot_axis) != 0):   
    # only perform the rotation if the plane was not xy to begin with!
    angle = np.arccos(np.dot(normal,z_axis)/(np.linalg.norm(normal)*np.linalg.norm(z_axis)))
    angle = np.rad2deg(angle)
    v1,v2,v3 = [vrotate(p, angle, rot_axis) for p in (v1,v2,v3)] # make list or dict eventually


print(v1,v2,v3)

[-0.65066344 -4.70684066  0.02032522] [-0.00330492  0.00054463  0.02032522] [ 0.12169508 -0.02005473  0.02032522]


In [ ]:

# Choose up to k points around each reference point as candidates for a new
# sample point
k = 5

# Minimum distance between samples
r = 0.5

#shift vertices to make everything positive
y_min = find_minmax(v1,v2,v3)[1]
v1,v2,v3 = [np.subtract(p, (0,y_min,0)) for p in (v1,v2,v3)] 
x_min = find_minmax(v1,v2,v3)[0]
v1,v2,v3 = [np.subtract(p, (x_min,0,0)) for p in (v1,v2,v3)] 

#find width and height of a transformed triangle

width, height = find_width_height( v1, v2, v3 )



# Cell side length
a = r/np.sqrt(2)
# Number of cells in the x- and y-directions of the grid
nx, ny = int(width / a) + 1, int(height / a) + 1

# A list of coordinates in the grid of cells
coords_list = [(ix, iy) for ix in range(nx) for iy in range(ny)]
# Initilalize the dictionary of cells: each key is a cell's coordinates, the
# corresponding value is the index of that cell's point's coordinates in the
# samples list (or None if the cell is empty).
cells = {coords: None for coords in coords_list}

def get_cell_coords(pt):
    """Get the coordinates of the cell that pt = (x,y) falls in."""

    return int(pt[0] // a), int(pt[1] // a)

def get_neighbours(coords):
    """Return the indexes of points in cells neighbouring cell at coords.

    For the cell at coords = (x,y), return the indexes of points in the cells
    with neighbouring coordinates illustrated below: ie those cells that could 
    contain points closer than r.

                                     ooo
                                    ooooo
                                    ooXoo
                                    ooooo
                                     ooo

    """

    dxdy = [(-1,-2),(0,-2),(1,-2),(-2,-1),(-1,-1),(0,-1),(1,-1),(2,-1),
            (-2,0),(-1,0),(1,0),(2,0),(-2,1),(-1,1),(0,1),(1,1),(2,1),
            (-1,2),(0,2),(1,2),(0,0)]
    neighbours = []
    for dx, dy in dxdy:
        neighbour_coords = coords[0] + dx, coords[1] + dy
        if not (0 <= neighbour_coords[0] < nx and
                0 <= neighbour_coords[1] < ny):
            # We're off the grid: no neighbours here.
            continue
        neighbour_cell = cells[neighbour_coords]
        if neighbour_cell is not None:
            # This cell is occupied: store this index of the contained point.
            neighbours.append(neighbour_cell)
    return neighbours

def point_valid(pt):
    """Is pt a valid point to emit as a sample?

    It must be no closer than r from any other point: check the cells in its
    immediate neighbourhood.

    """

    cell_coords = get_cell_coords(pt)
    for idx in get_neighbours(cell_coords):
        nearby_pt = samples[idx]
        # Squared distance between or candidate point, pt, and this nearby_pt.
        distance2 = (nearby_pt[0]-pt[0])**2 + (nearby_pt[1]-pt[1])**2
        if distance2 < r**2:
            # The points are too close, so pt is not a candidate.
            return False
    # All points tested: if we're here, pt is valid
    return True

def get_point(k, refpt):
    """Try to find a candidate point relative to refpt to emit in the sample.

    We draw up to k points from the annulus of inner radius r, outer radius 2r
    around the reference point, refpt. If none of them are suitable (because
    they're too close to existing points in the sample), return False.
    Otherwise, return the pt.

    """
    i = 0
    while i < k:
        rho, theta = np.random.uniform(r, 2*r), np.random.uniform(0, 2*np.pi)
        pt = refpt[0] + rho*np.cos(theta), refpt[1] + rho*np.sin(theta), 0
        if not (0 <= pt[0] < width and 0 <= pt[1] < height):
            # This point falls outside the domain of the grid, so try again.
            print(i,"cont", pt[0], width, pt[1], height)
            # This point falls outside the domain of the grid, so try again.
            i += 1
            continue
        if point_valid(pt) and is_on_face(pt, v1, v2, v3):
            return pt
        i += 1
    # We failed to find a suitable point in the vicinity of refpt.
    return False





# Pick a random point to start with.
pt = (np.random.uniform(0, width), np.random.uniform(0, height), 0)
while (not is_on_face(pt, v1,v2,v3)):
    pt = (np.random.uniform(0, width), np.random.uniform(0, height), 0)
    print("while",width, height, pt, v1, v3) 
print("while",width, height, pt, v1, v3)


samples = [pt]
vertices = [v1[0:2]]
vertices.append(v2)
vertices.append(v3)

# Our first sample is indexed at 0 in the samples list...
cells[get_cell_coords(pt)] = 0
# ... and it is active, in the sense that we're going to look for more points
# in its neighbourhood.
active = [0]

nsamples = 1
# As long as there are points in the active list, keep trying to find samples.
while active:
    # choose a random "reference" point from the active list.
    idx = np.random.choice(active)
    refpt = samples[idx]
    # Try to pick a new point relative to the reference point.
    pt = get_point(k, refpt)
    if pt:
        # Point pt is valid: add it to the samples list and mark it as active
        samples.append(pt)
        nsamples += 1
        active.append(len(samples)-1)
        cells[get_cell_coords(pt)] = len(samples) - 1
    else:
        # We had to give up looking for valid points near refpt, so remove it
        # from the list of "active" points.
        active.remove(idx)
   
#2D plot
#plt.scatter(*zip(*samples), color='g', alpha=0.6, lw=0)
plt.scatter(*zip(*vertices), color='r', alpha=0.6, lw=0)
plt.xlim(-0.25, width+0.25)
plt.ylim(-0.25, height+0.25)
plt.axis('on')
plt.show()

#3D plot
fig = plt.figure()
ax = Axes3D(fig)
ax.scatter(*zip(*vertices))
ax.scatter(*zip(*samples))
plt.show()
print(vertices)

>> 0.30087916800055936 2.9234076127319737
while 0.77235852051366 4.707385291195785 (0.23106055893902785, 3.2120826281808226, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.2965764373562703
while 0.77235852051366 4.707385291195785 (0.19124630080664007, 1.6654660450484526, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.49691660797174536
while 0.77235852051366 4.707385291195785 (0.28128868693339526, 0.4124684193223948, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.3051752354111819
while 0.77235852051366 4.707385291195785 (0.3259435526477268, 1.568441938648278, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.6287709610691252
while 0.77235852051366 4.707385291195785 (0.13119359635324532, 3.6999027717043482, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.300879

>> 0.30087916800055936 1.0513028160825346
while 0.77235852051366 4.707385291195785 (0.09547160725982043, 2.029561828801612, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.1700822156744288
while 0.77235852051366 4.707385291195785 (0.4897919199750019, 4.66800399180511, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.0223278858068374
while 0.77235852051366 4.707385291195785 (0.10697982532961535, 4.702195071877073, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 2.843090817170636
while 0.77235852051366 4.707385291195785 (0.061630206467811546, 1.39176549207338, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.9184842404795031
while 0.77235852051366 4.707385291195785 (0.6004190313329577, 1.175629345000644, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055

>> 0.30087916800055936 0.4644102492560221
while 0.77235852051366 4.707385291195785 (0.13769969116573666, 4.604121394103619, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 2.6350612337826393
while 0.77235852051366 4.707385291195785 (0.03418252263127012, 0.06315887391668382, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.4473268330541733
while 0.77235852051366 4.707385291195785 (0.6647455253807925, 1.5347753470591028, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 2.233304366962442
while 0.77235852051366 4.707385291195785 (0.15898353616037955, 2.393752047660357, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.107110890891525
while 0.77235852051366 4.707385291195785 (0.6650484236428313, 4.274907449882617, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800

while 0.77235852051366 4.707385291195785 (0.4095473561889344, 1.703513962120028, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.9112726144969052
while 0.77235852051366 4.707385291195785 (0.5885696665097335, 2.6224614957719785, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.0392392697882418
while 0.77235852051366 4.707385291195785 (0.34588081228822776, 0.6148875567670087, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.450960243874307
while 0.77235852051366 4.707385291195785 (0.7319603008186861, 0.9097975910421628, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 3.030404020461467
while 0.77235852051366 4.707385291195785 (0.5057197131981909, 3.216089670111475, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.3262227674193732
while 0.7723585205

while 0.77235852051366 4.707385291195785 (0.20140044993060188, 1.9698080301339411, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.6389737160785045
while 0.77235852051366 4.707385291195785 (0.6202535595912421, 3.8130320502849777, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.3388691361919742
while 0.77235852051366 4.707385291195785 (0.4417833371765817, 1.90205303937913, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.9089503574587265
while 0.77235852051366 4.707385291195785 (0.25367943240791374, 2.3365424369586214, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.630222415526981
while 0.77235852051366 4.707385291195785 (0.5914835657944468, 1.6343035048227295, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.8136635152418292
while 0.77235852

...

>> 0.30087916800055936 0.7476091238476947
while 0.77235852051366 4.707385291195785 (0.6447799208090007, 2.9449961424809983, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.0534064714640285
while 0.77235852051366 4.707385291195785 (0.24208343187054496, 2.424296934572776, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.7391974807468428
while 0.77235852051366 4.707385291195785 (0.7609195004528133, 2.478381711618521, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.9555405104069812
while 0.77235852051366 4.707385291195785 (0.29385662477722296, 4.3045187453913085, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.7070340847640009
while 0.77235852051366 4.707385291195785 (0.3090913698593609, 0.3215400605392362, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.3008791680

>> 0.30087916800055936 1.1769180444684972
while 0.77235852051366 4.707385291195785 (0.12904265719758579, 1.4248527298658724, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.627715200231898
while 0.77235852051366 4.707385291195785 (0.6595835442036109, 4.3325032033043485, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.31732535657794014
while 0.77235852051366 4.707385291195785 (0.022016630553463586, 1.2489350548635765, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.0117403482171035
while 0.77235852051366 4.707385291195785 (0.5975968072741776, 1.7839197325106335, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.7269070883877289
while 0.77235852051366 4.707385291195785 (0.4628677927618368, 2.8548117820111374, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.3008791

while 0.77235852051366 4.707385291195785 (0.09571554534496204, 1.210401438524613, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.6454837671580876
while 0.77235852051366 4.707385291195785 (0.3485143286950022, 0.5933626064670858, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.4798385289929126
while 0.77235852051366 4.707385291195785 (0.4366118168310701, 3.5899319533062295, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.5811731557303637
while 0.77235852051366 4.707385291195785 (0.19789858259387746, 0.5999154889080669, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.7742672317213916
while 0.77235852051366 4.707385291195785 (0.5973930351121048, 2.0999173844606895, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.4824266621121753
while 0.772358

>> 0.30087916800055936 2.2867814813974703
while 0.77235852051366 4.707385291195785 (0.09071541009586145, 1.3016352677829246, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.7260015212710593
while 0.77235852051366 4.707385291195785 (0.1833784547225314, 1.4397732889519477, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.40349739367641263
while 0.77235852051366 4.707385291195785 (0.690455199554648, 0.24139772522494923, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 3.351969691785649
while 0.77235852051366 4.707385291195785 (0.19757976522393092, 1.6055654682035645, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.4357070410483659
while 0.77235852051366 4.707385291195785 (0.26088784758224, 1.211123906514804, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800

while 0.77235852051366 4.707385291195785 (0.2048392278999809, 3.4102907287772353, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.547575904808454
while 0.77235852051366 4.707385291195785 (0.5165330550011858, 3.5159840574316306, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.32237705870485955
while 0.77235852051366 4.707385291195785 (0.4719032037259561, 3.8567899947426127, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.5874403646724362
while 0.77235852051366 4.707385291195785 (0.4024373397353709, 0.7200104597004343, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 1.6342943531117933
while 0.77235852051366 4.707385291195785 (0.27101025925962535, 1.3262950674874525, 0) [0.         0.         0.02032522] [0.77235852 4.68678593 0.02032522]
>> 0.30087916800055936 0.5613322783116802
while 0.772358

In [ ]:
#random for comparison

N = len(samples)   #generate the same num points as poisson-disc
print(N)
samples = []
while N>0:
    pt = (np.random.uniform(0,width), np.random.uniform(0,height))
    if is_on_face(pt, v1, v2, v3):
        samples.append(pt)
        N-=1
        
#2D plot
plt.scatter(*zip(*samples), color='g', alpha=0.6, lw=0)
plt.scatter(*zip(*vertices), color='r', alpha=0.6, lw=0)
plt.xlim(-0.25, width+0.25)
plt.ylim(-0.25, height+0.25)
plt.axis('on')
plt.show()

#3D plot
fig = plt.figure()
ax = Axes3D(fig)
ax.scatter(*zip(*vertices))
ax.scatter(*zip(*samples))
plt.show()

In [ ]:
#testing translations back for rotation specificlaly
from mpl_toolkits.mplot3d.art3d import Poly3DCollection

# v1 = (1,18,17)
# v2 = (7,0,7)
# v3 = (3,59,40)
v1 = v1_xyz[1806] #Choosing an arbitrary face to test on
v2 = v2_xyz[1806]
v3 = v3_xyz[1806]
points = []
points.append(v1)
points.append(v2)
points.append(v3)


fig = plt.figure()
ax = Axes3D(fig)
verts = [list((v1,v2,v3))]
# print(verts)
ax.add_collection3d(Poly3DCollection(verts))
ax.scatter(*zip(*(v1,v2,v3)))
ax.scatter(*v1)
ax.scatter(*v2)
ax.scatter(*v3)

ax.set_xlabel('X')
ax.set_ylabel('Y')
ax.set_zlabel('Z')
plt.show()
print(v1,v2,v3)

In [ ]:
origin_point = find_minmax(v1,v2,v3)[0:3]

# Translate face such that origin_point is the origin
translation = origin_point
v1,v2,v3,origin_point = [np.subtract(p, translation) for p in (v1,v2,v3,origin_point)] # make list or dict eventually


# rotate the face to become the xy-plane
angle = None
z_axis = (0.,0.,1.)
AB = np.subtract(v2,v1)
AC = np.subtract(v3,v1)

normal = np.cross(AB, AC)



rot_axis = np.cross(normal, z_axis)
if (np.linalg.norm(rot_axis) != 0):   
    # only perform the rotation if the plane was not xy to begin with!
    angle = np.arccos(np.dot(normal,z_axis)/(np.linalg.norm(normal)*np.linalg.norm(z_axis)))
    angle = np.rad2deg(angle)
    v1,v2,v3 = [vrotate(p, angle, rot_axis) for p in (v1,v2,v3)] # make list or dict eventually


fig = plt.figure()
ax = Axes3D(fig)
verts = [list((v1,v2,v3))]
# print(verts)
ax.add_collection3d(Poly3DCollection(verts))
ax.scatter(*zip(*(v1,v2,v3)))
ax.scatter(*v1)
ax.scatter(*v2)
ax.scatter(*v3)

ax.set_xlabel('X')
ax.set_ylabel('Y')
ax.set_zlabel('Z')
plt.show()
print(vertices)
print(v1,v2,v3)

In [ ]:
v1,v2,v3 = [np.add(p, (x_min,0,0)) for p in (v1,v2,v3)] # make list or dict eventually
v1,v2,v3 = [np.add(p, (0,y_min,0)) for p in (v1,v2,v3)] # make list or dict eventually
vertices = v1,v2,v3

if (np.linalg.norm(rot_axis) != 0): 
    vertices = [vrotate(p, angle, -rot_axis) for p in vertices] # make list or dict eventually
    print("rev rot", vertices)   
vertices = [np.add(p, translation) for p in vertices] # make list or dict eventually
#print(v1,v2,v3)    
print(vertices)


v1,v2,v3 = vertices
fig = plt.figure()
ax = Axes3D(fig)
verts = [list((v1,v2,v3))]
# print(verts)
ax.add_collection3d(Poly3DCollection(verts))
ax.scatter(*zip(*(v1,v2,v3)))
ax.scatter(*v1)
ax.scatter(*v2)
ax.scatter(*v3)

ax.set_xlabel('X')
ax.set_ylabel('Y')
ax.set_zlabel('Z')
plt.show()